In [ ]:
## Sparse vs. Dense matrices in Julia
using SparseArrays # This loads the sparse matrix package



In [ ]:
## Compare the performance of matrix-vector products for sparse and dense matrices
# We'll do this as a function of how many entries are non-zero in the matrix
using Random, BenchmarkTools, LinearAlgebra 
# n is the size of the sparse matrix
# p is the fraction of entries that are non-zero. 
function trial(n, p)
    Random.seed!(0)
    A = sprand(n, n, p) # Generate a random sparse matrix
    x = rand(n) # Generate a random vector
    y = zeros(n) # Allocate space for the result
    return (@btime(mul!($y, $A, $x))) # this does an in-place multiplication 
end
function dense_trial(n, p)
  Random.seed!(0)
  A = Matrix(sprand(n, n, p)) # Generate a random sparse matrix, but as dense 
  x = rand(n) # Generate a random vector
  y = zeros(n) # Allocate space for the result
  return (@btime(mul!($y, $A, $x))) # this does an in-place multiplication 
end
trial(100, 0.01) # Warm up the JIT compiler
dense_trial(100, 0.01) # Warm up the JIT compiler
trial(1000, 0.1) # Run a trial 
dense_trial(1000, 0.1) # Run a trial 




In [ ]:
##
trial(1000, 0.33) # Run a trial 
dense_trial(1000, 0.33) # Run a trial 



In [ ]:
## Let's make a little plot of this. 
function get_data(ns, ps)
  Random.seed!(0)
  results_sparse = zeros(length(ns), length(ps))
  results_dense = zeros(length(ns), length(ps))
  for (i, n) in pairs(ns) # pairs is a handy way of getting the index and value... 
    for (j, p) in pairs(ps)
      A = sprand(n, n, p) # Generate a random sparse matrix
      x = rand(n) # Generate a random vector
      y = zeros(n) # Allocate space for the result
      t = @elapsed(mul!(y, A, x)) # this does an in-place multiplication
      A = Matrix(A) # Convert to dense
      t_dense = @elapsed(mul!(y, A, x)) # this does an in-place multiplication
      results_sparse[i,j] = t
      results_dense[i,j] = t_dense
    end
  end
  return results_sparse, results_dense
end 
ns = [100, 200, 400, 800, 1600]
ps = [0.01, 0.05, 0.1, 0.2, 0.33, 0.5]
results_sparse, results_dense = get_data(ns, ps)



In [ ]:
## Now let's plot
using Plots
plot!(size=(800,600))
for (j, ps) in pairs(ps)
  plot!(ns, results_sparse[:,j], label="Sparse, p=$ps", marker=:circle)
  plot!(ns, results_dense[:,j], label="Dense, p=$ps", marker=:circle, linestyle=:dash)
end
xlabel!("Matrix size")
ylabel!("Time (s)")



In [ ]:
## Do this with lots of little plots, one for each p
plts = [] 
for (j,p) in pairs(ps)
  plt = plot(ns, results_sparse[:,j], label="Sparse", marker=:circle)
  plot!(plt, ns, results_dense[:,j], label="Dense", marker=:circle, linestyle=:dash)
  plot!(plt, yscale=:log10)
  title!(plt, "p = $p")
  push!(plts, plt) # add pl
end 
plot(plts..., layout=(3,2), size=(800,600)) # plot all the plots




In [ ]:
## Scopes in Julia
classvar1 = 5
function f1()
  i = 20 
  classvar1 = 10
  @show classvar1 
  classvar3 = 20 
  @show classvar3 
  for classvar2 in 1:10
    classvar3 = 30
    # println("classvar3 = ", classvar3)
    @show classvar3, classvar2
  end
  @show classvar1 # This will fail because classvar3 is not defined in this scope
  @show classvar3
end
f1()
println(classvar1)



In [ ]:
##
function testfunc(xs)
  for i in xs
    @show i 
  end 
end 
testfunc([1,5,10])